IMPORTING THE LIBRARIES

In [1]:
import logging
from langchain_community.vectorstores import PathwayVectorClient
from langchain_openai import OpenAIEmbeddings
from langchain.text_splitter import CharacterTextSplitter
from pathway.xpacks.llm.vector_store import VectorStoreServer
import os
import pathway as pw
import time
from dotenv import load_dotenv

In [2]:
load_dotenv()

False

In [3]:
from pathway.xpacks.llm.embedders import SentenceTransformerEmbedder
from pathway.xpacks.llm.splitters import TokenCountSplitter
from pathway.xpacks.llm.parsers import ParseUtf8
from pathway.xpacks.llm.vector_store import VectorStoreClient, VectorStoreServer

PATHWAY CONNECTOR FOR LABELLED DATA

In [4]:
PATHWAY_PORT = 8765
text_splitter = TokenCountSplitter(min_tokens=300,max_tokens=500)
embedder = SentenceTransformerEmbedder(model="BAAI/bge-large-en-v1.5")
parser=ParseUtf8()

In [5]:
# Define the conference mapping
conference_mapping = {
    "R006": "CVPR",
    "R007": "CVPR",
    "R008": "EMNLP",
    "R009": "EMNLP",
    "R0010": "KDD",
    "R0011": "KDD",
    "R0012": "NeurIPS",
    "R0013": "NeurIPS",
    "R0014": "TMLR",
    "R0015": "TMLR",
}

# Function to add conference metadata
def add_conference_metadata(metadata):
    # Ensure metadata is a dictionary
    if not isinstance(metadata, dict):
        metadata = {}

    # Extract name from metadata
    name = metadata.get("name", "")

    # Add conference label based on the mapping
    metadata["conference"] = conference_mapping.get(name, "Unknown")
    return metadata

In [6]:
table = pw.io.gdrive.read(object_id="1RKyDkAyW7cf09THED7Ms4LNBdeTDWnlK", service_user_credentials_file="credentials.json", mode="static", with_metadata=True)

In [7]:
processed_table = table.select(
    data=pw.this.data,
    _metadata=pw.apply(add_conference_metadata, pw.this._metadata)
)

In [8]:
print(table.column_names())


dict_keys(['_metadata', 'data'])


In [9]:
pw.debug.compute_and_print(processed_table,include_id=True)


[2025-01-18T05:42:08]:INFO:Preparing Pathway computation
[2025-01-18T05:42:08]:INFO:Enter read_snapshot method with reader Python
[2025-01-18T05:42:08]:INFO:PythonReader-0: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:08]:INFO:file_cache is only supported with oauth2client<4.0.0
[2025-01-18T05:42:20]:INFO:PythonReader-0: 1 entries (8 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:26]:INFO:PythonReader-0: 2 entries (4 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:32]:INFO:PythonReader-0: 2 entries (4 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:38]:INFO:PythonReader-0: 2 entries (4 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:44]:INFO:PythonReader-0: 2 entries (4 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:45]:INFO:PythonReader-0: 1 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:45]:WARNING:PythonReader-0: Closing the data source


            | data                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      

In [10]:
import io
from PyPDF2 import PdfReader

def parse_pdf(content: bytes) -> list[tuple[str, dict]]:
    try:
        reader = PdfReader(io.BytesIO(content))
        text = " ".join(page.extract_text() for page in reader.pages if page.extract_text())
        return [(text, {})]
    except Exception as e:
        print(f"Error parsing PDF: {e}")
        return []

def conditional_parser(content: bytes) -> list[tuple[str, dict]]:
    try:
        # Attempt UTF-8 parsing
        text = content.decode("utf-8")
        return [(text, {})]
    except UnicodeDecodeError:
        # Fallback to PDF parsing
        return parse_pdf(content)


In [11]:
vector_server = VectorStoreServer(
    table,
    parser=conditional_parser,
    embedder=embedder,
    splitter=text_splitter,
)
vector_server.run_server(host="127.0.0.1", port=8765, threaded=True, with_cache=True)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

/home/inevitable/kdsh_venv/lib/python3.12/site-packages/beartype/_util/hint/pep/utilpeptest.py:311: BeartypeDecorHintPep585DeprecationWarning: PEP 484 type hint typing.Sequence[str] deprecated by PEP 585. This hint is scheduled for removal in the first Python version released after October 5th, 2025. To resolve this, import this hint from "beartype.typing" rather than "typing". For further commentary and alternatives, see also:
    https://beartype.readthedocs.io/en/latest/api_roar/#pep-585-deprecations
  warn(


<Thread(VectorStoreServer, started 123382095939264)>

In [12]:
client = VectorStoreClient(
    host="127.0.0.1",
    port=PATHWAY_PORT,
)

PATHWAY CONNECTOR FOR UNLABELLED DATA

In [13]:
PATHWAY_PORT_UNLABELLED = 8766
# Process unlabelled data
unlabelled_table = pw.io.gdrive.read(
    object_id="1Y2Y0EsMalo26KcJiPYcAXh6UzgMNjh4u",  # Replace with actual object ID
    service_user_credentials_file="credentials.json",
    mode="static",
    with_metadata=True,
)

In [14]:
vector_server_unlabelled = VectorStoreServer(
    unlabelled_table,
    parser=conditional_parser,
    embedder=embedder,
    splitter=text_splitter,
)

[2025-01-18T05:42:46]:INFO:Preparing Pathway computation
[2025-01-18T05:42:46]:INFO:Removing obsolete metadata entry: 12-0-0
[2025-01-18T05:42:46]:INFO:Removing obsolete metadata entry: 12-0-1
[2025-01-18T05:42:46]:INFO:file_cache is only supported with oauth2client<4.0.0
[2025-01-18T05:42:46]:INFO:Worker 0 is on the version 14. The latest stable metadata version is Some(13)


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

[2025-01-18T05:42:46]:INFO:Enter read_snapshot method with reader Python
[2025-01-18T05:42:46]:INFO:Enter read_snapshot method with reader Python
[2025-01-18T05:42:46]:INFO:Enter read_snapshot method with reader Python
[2025-01-18T05:42:46]:INFO:Enter read_snapshot method with reader Python
[2025-01-18T05:42:46]:INFO:PythonReader-0: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:46]:INFO:PythonReader-1: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:46]:INFO:PythonReader-2: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:46]:INFO:PythonReader-3: 0 entries (1 minibatch(es)) have been sent to the engine


======== Running on http://127.0.0.1:8765 ========
(Press CTRL+C to quit)


In [15]:
vector_server_unlabelled.run_server(
    host="127.0.0.1", port=PATHWAY_PORT_UNLABELLED, threaded=True, with_cache=True
)

<Thread(VectorStoreServer, started 123381877835456)>

In [16]:
client_unlabelled = VectorStoreClient(host="127.0.0.1", port=PATHWAY_PORT_UNLABELLED)

GENERATING PROMPT

In [17]:
import csv
from langchain.llms import OpenAI

# Initialize the LLM
llm = OpenAI(model="gpt-4o", temperature=0)

def generate_prompt_with_rationale(labeled_data, unlabelled_embedding, conference_info):
    """
    Generate an LLM prompt including rationale generation.
    """
    labeled_papers_prompt = "\n".join(
        f"Embedding: {data['embedding']}\nConference: {data['conference']}"
        for data in labeled_data
    )

    unlabeled_paper_prompt = f"Embedding: {unlabelled_embedding}"

    prompt = f"""
    The labeled research papers with embeddings and conference information:
    {labeled_papers_prompt}

    The unlabelled research paper embedding:
    {unlabeled_paper_prompt}

    Conference descriptions:
    {conference_info}

    Instructions:
    1. Determine if the unlabelled paper embedding is similar to any labeled paper embedding.
    2. If yes, assign the conference of the most similar labeled paper.
    3. If no, classify the unlabelled paper into one of the conferences using the conference descriptions.
    4. Provide a rationale explaining why the unlabelled research paper was assigned to the selected conference.
    Output the assigned conference and the rationale.
    """
    return prompt

/tmp/ipykernel_71471/2959129995.py:5: LangChainDeprecationWarning: The class `OpenAI` was deprecated in LangChain 0.0.10 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-openai package and should be used instead. To use it run `pip install -U :class:`~langchain-openai` and import as `from :class:`~langchain_openai import OpenAI``.
  llm = OpenAI(model="gpt-4o", temperature=0)
[2025-01-18T05:42:47]:INFO:Preparing Pathway computation
[2025-01-18T05:42:47]:INFO:Removing obsolete metadata entry: 13-0-1
[2025-01-18T05:42:47]:INFO:Removing obsolete metadata entry: 13-0-0
[2025-01-18T05:42:47]:INFO:file_cache is only supported with oauth2client<4.0.0
[2025-01-18T05:42:47]:INFO:Worker 0 is on the version 15. The latest stable metadata version is Some(14)
[2025-01-18T05:42:47]:INFO:Enter read_snapshot method with reader Python
[2025-01-18T05:42:47]:INFO:Enter read_snapshot method with reader Python
[2025-01-18T05:42:47]:INFO:Enter read_snapshot method

======== Running on http://127.0.0.1:8766 ========
(Press CTRL+C to quit)


ValidationError: 1 validation error for OpenAI
  Value error, Did not find openai_api_key, please add an environment variable `OPENAI_API_KEY` which contains it, or pass `openai_api_key` as a named parameter. [type=value_error, input_value={'temperature': 0, 'model...ne, 'http_client': None}, input_type=dict]
    For further information visit https://errors.pydantic.dev/2.9/v/value_error

[2025-01-18T05:42:48]:INFO:PythonReader-0: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:48]:INFO:PythonReader-1: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:48]:INFO:PythonReader-2: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:48]:INFO:PythonReader-3: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:48]:INFO:PythonReader-4: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:48]:INFO:PythonReader-5: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:48]:INFO:PythonReader-6: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:48]:INFO:PythonReader-7: 0 entries (1 minibatch(es)) have been sent to the engine
[2025-01-18T05:42:58]:INFO:PythonReader-0: 1 entries (7 minibatch(es)) have been sent to the engine


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:

def call_llm_with_rationale(prompt):
    """
    Call the LLM to classify the paper and generate rationale.
    """
    response = llm(prompt)
    response_lines = response.strip().split("\n")
    assigned_conference = response_lines[0].strip()  # Extract the conference
    rationale = "\n".join(response_lines[1:]).strip()  # Extract the rationale
    return assigned_conference, rationale

PASSING THE PROMPT TO LLM 

In [ ]:
def process_unlabelled_papers_with_rationale(labeled_data, client_unlabelled):
    """
    Process all unlabelled papers and generate conference assignments and rationales using the LLM.
    """
    conference_info = """
    prompt += '''- CVPR (Conference on Computer Vision and Pattern Recognition): Papers in the main technical program must describe high-quality, original research. Topics of interest cover all aspects of computer vision and pattern recognition including, but not limited to:
    FLIP (Flipping labels to inject poision)
    pixel deflection
    3D from multi-view and sensors  
    3D from single images  
    Adversarial attack and defense
    Autonomous driving
    Biometrics  
    Computational imaging  
    Computer vision for social good  
    Computer vision theory  
    Datasets and evaluation  
    Deep learning architectures and techniques  
    Document analysis and understanding  
    Efficient and scalable vision  
    Embodied vision: Active agents, simulation
    Event-based cameras
    Explainable computer vision  
    Humans: Face, body, pose, gesture, movement
    Image and video synthesis and generation  
    Low-level vision  
    Machine learning (other than deep learning)
    Medical and biological vision, cell microscopy
    Multimodal learning
    Optimization methods (other than deep learning)
    Photogrammetry and remote sensing  
    Physics-based vision and shape-from-X  
    Recognition: Categorization, detection, retrieval  
    Representation learning  
    Computer Vision for Robotics  
    Scene analysis and understanding  
    Segmentation, grouping and shape analysis  
    Self-, semi-, meta- and unsupervised learning
    Transfer/ low-shot/ continual/ long-tail learning  
    Transparency, fairness, accountability, privacy and ethics in vision  
    Video: Action and event understanding 
    Video: Low-level analysis, motion, and tracking  
    Vision + graphics  
    Vision, language, and reasoning  
    Vision applications and systems\n'''

    prompt += '''- EMNLP (Empirical Methods in Natural Language Processing): EMNLP 2024 aims to have a broad technical program. Relevant topics for the conference include, but are not limited to:

    Computational Social Science and Cultural Analytics
    Dialogue and Interactive Systems
    Discourse and Pragmatics
    Low-resource Methods for NLP
    Ethics, Bias, and Fairness
    Generation
    Information Extraction
    Information Retrieval and Text Mining
    Interpretability and Analysis of Models for NLP
    Linguistic theories, Cognitive Modeling and Psycholinguistics
    Machine Learning for NLP
    Machine Translation
    Multilinguality and Language Diversity
    Multimodality and Language Grounding to Vision, Robotics and Beyond
    Phonology, Morphology and Word Segmentation
    Question Answering
    Resources and Evaluation
    Semantics: Lexical, Sentence-level Semantics, Textual Inference and Other areas
    Sentiment Analysis, Stylistic Analysis, and Argument Mining
    Speech processing and spoken language understanding
    Summarization
    Syntax: Tagging, Chunking and Parsing
    NLP Applications
    Special Theme: Efficiency in Model Algorithms, Training, and Inference\n'''

    prompt += '''- KDD (Knowledge Discovery and Data Mining): For the research track, we invite submission of papers describing innovative research on all aspects of knowledge discovery and data science, ranging from theoretical foundations to novel models and algorithms for data science problems in science, business, medicine, and engineering. Visionary papers on new and emerging topics are also welcome, as are application-oriented papers that make innovative technical contributions to research. Topics of interest include, but are not limited to:

    Data Science: Methods for analyzing social networks, time series, sequences, streams, text, web, graphs, rules, patterns, logs, IoT data, spatio-temporal data, biological data, scientific and business data; recommender systems, computational advertising, multimedia, finance, bioinformatics.
    Big Data: Large-scale systems for data analysis, machine learning, optimization, sampling, summarization; parallel and distributed data science (cloud, map-reduce, federated learning); novel algorithmic and statistical techniques for big data; algorithmically-efficient data transformation and integration.
    Foundations: Models and algorithms, asymptotic analysis; model selection, dimensionality reduction, relational/structured learning, matrix and tensor methods, probabilistic and statistical methods; deep learning, transfer learning, representation learning, meta learning, reinforcement learning; classification, clustering, regression, semi-supervised learning, self-supervised learning, few shot learning and unsupervised learning; personalization, security and privacy, visualization; fairness, interpretability, ethics and robustness.
    it includes debruijn graphs 
    for example the abstract of research paper in KDD-Parkinson’s disease (PD) is a progressive neurodegenerative disorder that leads to motor symptoms, including gait
impairment. The effectiveness of levodopa therapy, a common treatment for PD, can fluctuate, causing periods of
improved mobility ("on" state) and periods where symptoms re-emerge ("off" state). These fluctuations impact
gait speed and increase in severity as the disease progresses. This paper proposes a transformer-based method that
uses both Received Signal Strength Indicator (RSSI) and accelerometer data from wearable devices to enhance
indoor localization accuracy. A secondary goal is to determine if indoor localization, particularly in-home gait
speed features (like the time to walk between rooms), can be used to identify motor fluctuations by detecting if a
person with PD is taking their levodopa medication or not. The method is evaluated using a real-world dataset
collected in a free-living setting, where movements are varied and unstructured. Twenty-four participants, living
in pairs (one with PD and one control), resided in a sensor-equipped smart home for five days. The results show
that the proposed network surpasses other methods for indoor localization. The evaluation of the secondary goal
reveals that accurate room-level localization, when converted into in-home gait speed features, can accurately
predict whether a PD participant is taking their medication or not.\n'''

    prompt += '''- NeurIPS (Neural Information Processing Systems): This conference invites submissions presenting new and original research on a variety of machine learning topics.•	General Machine Learning: Including classification, unsupervised learning, transfer learning, and reinforcement learning.
	•	Neuroscience and Cognitive Science: Studies that bridge machine learning with insights from neuroscience and cognitive science.
	•	Robotics: Integration of machine learning techniques in robotic perception, control, and decision-making..
	•	Theory: Theoretical foundations underpinning machine learning algorithms and statistical learning.
	•	Applications: Innovative applications of machine learning in various domains, finance, and social sciences.
    
    for example abstract of research paper 
    
    eg. 1 Regression tasks, while aiming to model relationships across the entire input space,

are often constrained by limited training data. Nevertheless, if the hypothesis func-
tions can be represented effectively by the data, there is potential for identifying a

model that generalizes well. This paper introduces the Neural Restricted Isometry
Property (NeuRIPs), which acts as a uniform concentration event that ensures all
shallow ReLU networks are sketched with comparable quality. To determine the
sample complexity necessary to achieve NeuRIPs, we bound the covering numbers

of the networks using the Sub-Gaussian metric and apply chaining techniques. As-
suming the NeuRIPs event, we then provide bounds on the expected risk, applicable

to networks within any sublevel set of the empirical risk. Our results show that all
networks with sufficiently small empirical risk achieve uniform generalization.\n'''

    prompt += '''- TMLR (Transactions on Machine Learning Research): TMLR’s objective is to publish original papers that contribute to the understanding of the computational and mathematical principles that enable intelligence through learning, be it in brains or in machines.
It includes papers with positional encoding 
To this end, TMLR invites authors to submit papers that contain
it includes topics TFGNN , Training Free Graph Neural Network 
new algorithms with sound empirical validation, optionally with justification of theoretical, psychological, or biological nature;
experimental and/or theoretical studies yielding new insight into the design and behavior of learning in intelligent systems;
accounts of applications of existing techniques that shed light on the strengths and weaknesses of the methods;
formalization of new learning tasks (e.g., in the context of new applications) and of methods for assessing performance on those tasks;
development of new analytical frameworks that advance theoretical studies of practical learning methods;
computational models of natural learning systems at the behavioral or neural level;
reproducibility studies of previously published results or claims;
new approaches for analysis, visualization, and understanding of artificial or biological learning systems;
surveys that draw new connections, highlight trends, and suggest new problems in an area.


for example the abstract of TMLR research papers 

e.g 1 This research examines a specific category of structured nonconvex-nonconcave min-max problems that demon-
strate a characteristic known as weak Minty solutions. This concept, which has only recently been defined, has

already demonstrated its effectiveness by encompassing various generalizations of monotonicity at the same time.
We establish new convergence findings for an enhanced variant of the optimistic gradient method (OGDA) within
this framework, achieving a convergence rate of 1/k for the most effective iteration, measured by the squared
operator norm, a result that aligns with the extragradient method (EG). Furthermore, we introduce a modified
version of EG that incorporates an adaptive step size, eliminating the need for prior knowledge of the problem’s
specific parameters.

e.g 2 Deep generative models, particularly diffusion models, are a significant family within deep learning. This study
provides a precise upper limit for the Wasserstein distance between a learned distribution by a diffusion model
and the target distribution. In contrast to earlier research, this analysis does not rely on presumptions regarding
the learned score function. Furthermore, the findings are applicable to any data-generating distributions within
restricted instance spaces, even those lacking a density relative to the Lebesgue measure, and the upper limit is not
exponentially dependent on the ambient space dimension. The primary finding expands upon recent research by
Mbacke et al. (2023), and the proofs presented are fundamental.\n'''

    
    """
    unlabelled_results = client_unlabelled(query="Fetch all unlabelled papers")
    results = []

    for paper in unlabelled_results:
        unlabelled_embedding = paper["embedding"]

        # Generate the LLM prompt
        prompt = generate_prompt_with_rationale(labeled_data, unlabelled_embedding, conference_info)

        # Call the LLM and get the conference and rationale
        assigned_conference, rationale = call_llm_with_rationale(prompt)

        # Store the result
        results.append({
            "Paper ID": paper["id"],
            "Classification": f"Conference: {assigned_conference}",
            "Reasoning": rationale
        })

    return results

SAVING TO CSV

In [ ]:
def save_results_to_csv(results, output_filename="results.csv"):
    """
    Save classification results to a CSV file in the specified format.
    """
    headers = ["Paper ID", "Publishable", "Conference", "Rationale"]

    with open(output_filename, mode="w", newline="", encoding="utf-8") as csvfile:
        writer = csv.writer(csvfile)
        writer.writerow(headers)

        for result in results:
            paper_id = result.get("Paper ID", "N/A")
            classification = result.get("Classification", "Conference: NA")
            rationale = result.get("Reasoning", "NA")

            # Extract conference name
            conference = classification.split(": ")[-1].strip().upper()

            # Determine publishability
            if conference == "NA":
                publishable = 0
                rationale = "NA"
            else:
                publishable = 1

            writer.writerow([paper_id, publishable, conference, rationale])

    print(f"Results have been saved to {output_filename}")

THE MAIN

In [ ]:

# Fetch labeled papers
labeled_results = client(query="Fetch all labeled papers")
labeled_data = [
    {"embedding": doc["embedding"], "conference": doc["metadata"]["conference"]}
    for doc in labeled_results
]

# Process all unlabelled papers
results = process_unlabelled_papers_with_rationale(labeled_data, client_unlabelled)

# Save the results to CSV
save_results_to_csv(results, output_filename="results.csv")